# Tutorial - build MNB with sklearn

This tutorial demonstrates how to use the Sci-kit Learn (sklearn) package to build Multinomial Naive Bayes model, rank features, and use the model for prediction. 

The data from the Kaggle Sentiment Analysis on Movie Review Competition are used in this tutorial. Check out the details of the data and the competition on Kaggle.
https://www.kaggle.com/c/sentiment-analysis-on-movie-reviews

The tutorial also includes sample code to prepare your prediction result for submission to Kaggle. Although the competition is over, you can still submit your prediction to get an evaluation score.

This revised script changed two places in the original script:
(1) Exercise A: replaced the outdated "itemfreq" function with new one so no more warnings
(2) Exercise C: replace the "coef_" variable with the "feature_log_prob_" variable. Although the sklearn manual said coef_ mirrors feature_log_prob_, we found that in case of binary classification, coef_ has only one dimension but feature_log_prob_ keeps the original two dimensions of positive and negative conditional probs. The code was also cleaned and simplified.# Step 1: Read in data

In [1]:


# read in the training data

# the data set includes four columns: PhraseId, SentenceId, Phrase, Sentiment
# In this data set a sentence is further split into phrases 
# in order to build a sentiment classification model
# that can not only predict sentiment of sentences but also shorter phrases

# A data example:
# PhraseId SentenceId Phrase Sentiment
# 1 1 A series of escapades demonstrating the adage that what is good for the goose is also good for the gander , some of which occasionally amuses but none of which amounts to much of a story .1

# the Phrase column includes the training examples
# the Sentiment column includes the training labels
# "0" for very negative
# "1" for negative
# "2" for neutral
# "3" for positive
# "4" for very positive

import numpy as np
import pandas as p
train=p.read_csv("kaggle-sentiment/train.tsv", delimiter='\t')
y=train['Sentiment'].values
X=train['Phrase'].values

train[:5]

PhraseId  SentenceId                                             Phrase  \
0         1           1  A series of escapades demonstrating the adage ...   
1         2           1  A series of escapades demonstrating the adage ...   
2         3           1                                           A series   
3         4           1                                                  A   
4         5           1                                             series   

   Sentiment  
0          1  
1          2  
2          2  
3          2  
4          2

# Step 2: Split train/test data for hold-out test

In [2]:
# check the sklearn documentation for train_test_split
# http://scikit-learn.org/stable/modules/generated/sklearn.model_selection.train_test_split.html
# "test_size" : float, int, None, optional
# If float, should be between 0.0 and 1.0 and represent the proportion of the dataset to include in the test split. 
# If int, represents the absolute number of test samples. 
# If None, the value is set to the complement of the train size. 
# By default, the value is set to 0.25. The default will change in version 0.21. It will remain 0.25 only if train_size is unspecified, otherwise it will complement the specified train_size.    

from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=None, random_state=0)

print(X_train.shape, y_train.shape, X_test.shape, y_test.shape)
print(X_train[0])
print(y_train[0])
print(X_test[0])
print(y_test[0])

(117045,) (117045,) (39015,) (39015,)
illusion
2
escape movie
2


Sample output from the code above:

(93636,) (93636,) (62424,) (62424,)
almost in a class with that of Wilde
3
escape movie
2

# Step 2.1 Data Checking

In [3]:
# Check how many training examples in each category
# this is important to see whether the data set is balanced or skewed

unique, counts = np.unique(y_train, return_counts=True)
print(np.asarray((unique, counts)))

unique, counts = np.unique(y_test, return_counts=True)
print(np.asarray((unique, counts))) 

[[    0     1     2     3     4]
 [ 5228 20482 59601 24837  6897]]
[[    0     1     2     3     4]
 [ 1844  6791 19981  8090  2309]]


The sample output shows that the data set is skewed with 47718/93636=51% "neutral" examples. All other categories are smaller.

{0, 1, 2, 3, 4}
[[    0  4141]
 [    1 16449]
 [    2 47718]
 [    3 19859]
 [    4  5469]]

# Exercise A

In [4]:
# Print out the category distribution in the test data set. 
# Is the test data set's category distribution similar to the training data set's?

# Your code starts here
training_labels = set(y_train)
print(training_labels)
from scipy.stats import itemfreq
training_category_dist = itemfreq(y_train)
# ^^ apparently being depreciated 
training_cateory_dist = np.unique(y_train, return_counts=True)
print(training_category_dist)
testing_category_dist = np.unique(y_test, return_counts=True)
print(testing_category_dist)


{0, 1, 2, 3, 4}
[[    0  5228]
 [    1 20482]
 [    2 59601]
 [    3 24837]
 [    4  6897]]
(array([0, 1, 2, 3, 4]), array([ 1844,  6791, 19981,  8090,  2309]))


/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:8: DeprecationWarning: `itemfreq` is deprecated!
`itemfreq` is deprecated and will be removed in a future version. Use instead `np.unique(..., return_counts=True)`
  


In [5]:
import matplotlib.pyplot as plt
plt.bar(testing_category_dist[0], testing_category_dist[1], align='center', alpha=0.5)
plt.ylabel('Num Reviews')
plt.title('Test Distribution')
plt.show()

<Figure size 640x480 with 1 Axes>

In [11]:
## REPLICATING THE CODE
training_labels = set(y_train)
print(training_labels)
from scipy.stats import itemfreq
# training_category_dist = itemfreq(y_train)
# ^^ being depreciated 
training_cateory_dist = np.unique(y_train, return_counts=True)
print(training_category_dist)
testing_category_dist = np.unique(y_test, return_counts=True)
print(testing_category_dist)

## PLOTTING TEST AND TRAIN
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

unique, counts = np.unique(y_train, return_counts=True)
train_arr = np.asarray((unique, counts))

unique, counts = np.unique(y_test, return_counts=True)
test_arr = np.asarray((unique, counts))

# x = testing_category_dist[0].tolist()
# print(x)
# train = train_arr[1].tolist()
# print(z)
# test = test_arr[1].tolist()
# print(k)

# df = pd.DataFrame(zip(x*2, ["train"]*len(x)+["test"]*len(x), train+test), columns=["sentiment", "dataset", "reviews"])
# print(df)
# plt.figure(figsize=(10, 6))
# sns.barplot(x="sentiment", hue="dataset", y="reviews", data=df)
# plt.show()

{0, 1, 2, 3, 4}
[[    0  5228]
 [    1 20482]
 [    2 59601]
 [    3 24837]
 [    4  6897]]
(array([0, 1, 2, 3, 4]), array([ 1844,  6791, 19981,  8090,  2309]))


In [14]:
# df = pd.DataFrame(zip(x*2, ["z"]*5+["k"]*5, z+k), columns=["sentiment", "kind", "reviews"])
# ["z"]*5+["k"]*5
# z+k

# Step 3: Vectorization

In [15]:
# sklearn contains two vectorizers

# CountVectorizer can give you Boolean or TF vectors
# http://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.CountVectorizer.html

# TfidfVectorizer can give you TF or TFIDF vectors
# http://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.TfidfVectorizer.html

# Read the sklearn documentation to understand all vectorization options

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer

# several commonly used vectorizer setting

#  unigram boolean vectorizer, set minimum document frequency to 5
unigram_bool_vectorizer = CountVectorizer(encoding='latin-1', binary=True, min_df=5, stop_words='english')

#  unigram term frequency vectorizer, set minimum document frequency to 5
unigram_count_vectorizer = CountVectorizer(encoding='latin-1', binary=False, min_df=5, stop_words='english')

#  unigram and bigram term frequency vectorizer, set minimum document frequency to 5
gram12_count_vectorizer = CountVectorizer(encoding='latin-1', ngram_range=(1,2), min_df=5, stop_words='english')

#  unigram tfidf vectorizer, set minimum document frequency to 5
unigram_tfidf_vectorizer = TfidfVectorizer(encoding='latin-1', use_idf=True, min_df=5, stop_words='english')






## Step 3.1: Vectorize the training data

In [17]:
# The vectorizer can do "fit" and "transform"
# fit is a process to collect unique tokens into the vocabulary
# transform is a process to convert each document to vector based on the vocabulary
# These two processes can be done together using fit_transform(), or used individually: fit() or transform()

# fit vocabulary in training documents and transform the training documents into vectors
X_train_vec = unigram_count_vectorizer.fit_transform(X_train)

# check the content of a document vector

# check the size of the constructed vocabulary
print(len(unigram_count_vectorizer.vocabulary_))

# print out the first 10 items in the vocabulary
print(list(unigram_count_vectorizer.vocabulary_.items())[:10])

# check word index in vocabulary
print(unigram_count_vectorizer.vocabulary_.get('imaginative'))

13247
[('illusion', 5790), ('gore', 5084), ('entertaining', 3918), ('somewhat', 10851), ('standardized', 11090), ('surprise', 11484), ('mayhem', 7255), ('geared', 4915), ('maximum', 7253), ('comfort', 2241)]
5800


Sample output:

(93636, 11967)
[[0 0 0 ..., 0 0 0]]
11967
[('imaginative', 5224), ('tom', 10809), ('smiling', 9708), ('easy', 3310), ('diversity', 3060), ('impossibly', 5279), ('buy', 1458), ('sentiments', 9305), ('households', 5095), ('deteriorates', 2843)]
5224

## Step 3.2: Vectorize the test data

In [18]:
# use the vocabulary constructed from the training data to vectorize the test data. 
# Therefore, use "transform" only, not "fit_transform", 
# otherwise "fit" would generate a new vocabulary from the test data

X_test_vec = unigram_count_vectorizer.fit_transform(X_test)

# print out #examples and #features in the test set
print(X_test_vec.shape)

(39015, 6429)


Sample output:

(62424, 14324)

# Exercise B

In [19]:
# In the above sample code, the term-frequency vectors were generated for training and test data.

# Some people argue that 
# because the MultinomialNB algorithm is based on word frequency, 
# we should not use boolean representation for MultinomialNB.
# While in theory it is true, you might see people use boolean representation for MultinomialNB
# especially when the chosen tool, e.g. Weka, does not provide the BernoulliNB algorithm.

# sklearn does provide both MultinomialNB and BernoulliNB algorithms.
# http://scikit-learn.org/stable/modules/generated/sklearn.naive_bayes.BernoulliNB.html
# You will practice that later

# In this exercise you will vectorize the training and test data using boolean representation
# You can decide on other options like ngrams, stopwords, etc.

# Your code starts here
# test_bool = unigram_count_vectorizer.transform(X_test)
# train_bool = unigram_count_vectorizer.transform(X_train)





In [20]:
# This kept giving me this error
# NotFittedError: CountVectorizer - Vocabulary wasn't fitted.

test_bool = unigram_bool_vectorizer.fit_transform(X_test)
train_bool = unigram_bool_vectorizer.fit_transform(X_train)

# # So I did this
# import sklearn
# vocabulary_to_load = X_test
# loaded_vectorizer = sklearn.feature_extraction.text.CountVectorizer(ngram_range=(1,
#                                         2), binary = True, min_df=1, vocabulary=vocabulary_to_load)
# loaded_vectorizer._validate_vocabulary()
# print('loaded_vectorizer.get_feature_names(): {0}'.
#   format(loaded_vectorizer.get_feature_names()))
train_bool
test_bool

<39015x6429 sparse matrix of type '<class 'numpy.int64'>'
	with 124934 stored elements in Compressed Sparse Row format>

# Step 4: Train a MNB classifier

In [21]:
# import the MNB module
from sklearn.naive_bayes import MultinomialNB

# initialize the MNB model
nb_clf= MultinomialNB()

# use the training data to train the MNB model
nb_clf.fit(X_train_vec,y_train)

MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True)

# Step 4.1 Interpret a trained MNB model

In [22]:
## interpreting naive Bayes models
## by consulting the sklearn documentation you can also find out feature_log_prob_, 
## which are the conditional probabilities
## http://scikit-learn.org/stable/modules/generated/sklearn.naive_bayes.MultinomialNB.html

# the code below will print out the conditional prob of the word "worthless" in each category
# sample output
# -8.98942647599 -> logP('worthless'|very negative')
# -11.1864401922 -> logP('worthless'|negative')
# -12.3637684625 -> logP('worthless'|neutral')
# -11.9886066961 -> logP('worthless'|positive')
# -11.0504454621 -> logP('worthless'|very positive')
# the above output means the word feature "worthless" is indicating "very negative" 
# because P('worthless'|very negative) is the greatest among all conditional probs

unigram_count_vectorizer.vocabulary_.get('worthless')
for i in range(0,5):
    print(nb_clf.feature_log_prob_[i][unigram_count_vectorizer.vocabulary_.get('worthless')])

-10.686292605026608
-9.943179308577442
-10.682714947521708
-11.695088675894803
-10.832635277912791


Sample output:

-8.5389826392
-10.6436375867
-11.8419845779
-11.4778370023
-10.6297551464

In [23]:
# sort the conditional probability for category 0 "very negative"
# print the words with highest conditional probs
# these can be words popular in the "very negative" category alone, or words popular in all cateogires

feature_ranks = sorted(zip(nb_clf.feature_log_prob_[0], unigram_count_vectorizer.get_feature_names()))
very_negative_features = feature_ranks[-10:]
print(very_negative_features)

[(-6.409626486010553, 'anachronistic'), (-6.368804491490298, 'sharp'), (-6.304265970352727, 'knowing'), (-6.142997822756604, 'mermaid'), (-6.051563616796972, 'anakin'), (-5.994944722797465, 'lovely'), (-5.803490682440238, 'fleshed'), (-5.7959434768048546, 'enduring'), (-4.8993952236599005, 'chiefly'), (-4.8226614294285115, 'purpose')]


# Exercise C

In [24]:
sorted(zip(nb_clf.feature_log_prob_[0], unigram_count_vectorizer.get_feature_names()))

[(-10.686292605026608, '12'),
 (-10.686292605026608, '163'),
 (-10.686292605026608, '18'),
 (-10.686292605026608, '19'),
 (-10.686292605026608, '1920'),
 (-10.686292605026608, '1940s'),
 (-10.686292605026608, '1958'),
 (-10.686292605026608, '1970s'),
 (-10.686292605026608, '1984'),
 (-10.686292605026608, '1999'),
 (-10.686292605026608, '19th'),
 (-10.686292605026608, '20'),
 (-10.686292605026608, '2000'),
 (-10.686292605026608, '2002'),
 (-10.686292605026608, '21st'),
 (-10.686292605026608, '30'),
 (-10.686292605026608, '300'),
 (-10.686292605026608, '3000'),
 (-10.686292605026608, '3d'),
 (-10.686292605026608, '40'),
 (-10.686292605026608, '50'),
 (-10.686292605026608, '50s'),
 (-10.686292605026608, '52'),
 (-10.686292605026608, '7th'),
 (-10.686292605026608, '80s'),
 (-10.686292605026608, '84'),
 (-10.686292605026608, '85'),
 (-10.686292605026608, '88'),
 (-10.686292605026608, '90s'),
 (-10.686292605026608, '95'),
 (-10.686292605026608, 'abagnale'),
 (-10.686292605026608, 'abc'),
 (-

In [25]:
# calculate log ratio of conditional probs

# In this exercise you will calculate the log ratio 
# between conditional probs in the "very negative" category
# and conditional probs in the "very positive" category,
# and then sort and print out the top and bottom 10 words

# the conditional probs for the "very negative" category is stored in nb_clf.feature_log_prob_[0]
# the conditional probs for the "very positive" category is stored in nb_clf.feature_log_prob_[4]

# You can consult with similar code in week 4's sample script on feature weighting
# Note that in sklearn's MultinomialNB the conditional probs have been converted to log values.

# Your code starts here

very_negative = sorted(zip(nb_clf.feature_log_prob_[0], unigram_count_vectorizer.get_feature_names()))
very_positive = sorted(zip(nb_clf.feature_log_prob_[4], unigram_count_vectorizer.get_feature_names()))

very_negative[:10]
very_positive[:10]
# Your code ends here

'''
[(-4.6685160302515563, 'worst'), (-4.1676048635427438, 'bad'), (-3.9753688496916109, 'stupid'), (-3.8602995199068237, 'worse'), (-3.7576453658467397, 'contrived'), (-3.7576453658467397, 'unfunny'), (-3.7302463916586257, 'awful'), (-3.7020755146919289, 'poorly'), (-3.6432350146689956, 'waste'), (-3.5479248348646717, 'pathetic')]
[(3.5668446135017922, 'rich'), (3.6374621807157457, 'wonderful'), (3.8045162653789113, 'excellent'), (3.8422565933617587, 'gorgeous'), (3.8786242375326339, 'touching'), (3.9308099907032039, 'solid'), (3.9641464109707956, 'powerful'), (4.027659816693121, 'beautifully'), (4.1437319879458752, 'beautiful'), (4.2352991814713654, 'moving')]
'''

"\n[(-4.6685160302515563, 'worst'), (-4.1676048635427438, 'bad'), (-3.9753688496916109, 'stupid'), (-3.8602995199068237, 'worse'), (-3.7576453658467397, 'contrived'), (-3.7576453658467397, 'unfunny'), (-3.7302463916586257, 'awful'), (-3.7020755146919289, 'poorly'), (-3.6432350146689956, 'waste'), (-3.5479248348646717, 'pathetic')]\n[(3.5668446135017922, 'rich'), (3.6374621807157457, 'wonderful'), (3.8045162653789113, 'excellent'), (3.8422565933617587, 'gorgeous'), (3.8786242375326339, 'touching'), (3.9308099907032039, 'solid'), (3.9641464109707956, 'powerful'), (4.027659816693121, 'beautifully'), (4.1437319879458752, 'beautiful'), (4.2352991814713654, 'moving')]\n"

Sample output for print(log_ratios[0])

-0.838009538739

# Step 5: Test the MNB classifier

In [26]:
# test the classifier on the test data set, print accuracy score

nb_clf.score(X_test_vec,y_test)

ValueError: dimension mismatch

In [27]:
# print confusion matrix (row: ground truth; col: prediction)

from sklearn.metrics import confusion_matrix
y_pred = nb_clf.fit(X_train_vec, y_train).predict(X_test_vec)
cm=confusion_matrix(y_test, y_pred, labels=[0,1,2,3,4])
print(cm)

ValueError: dimension mismatch

In [28]:
# print classification report

from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
print(precision_score(y_test, y_pred, average=None))
print(recall_score(y_test, y_pred, average=None))

from sklearn.metrics import classification_report
target_names = ['0','1','2','3','4']
print(classification_report(y_test, y_pred, target_names=target_names))

NameError: name 'y_pred' is not defined

# Step 5.1 Interpret the prediction result

In [38]:
## find the calculated posterior probability
posterior_probs = nb_clf.predict_proba(X_test_vec)

## find the posterior probabilities for the first test example
print(posterior_probs[0])

# find the category prediction for the first test example
y_pred = nb_clf.predict(X_test_vec)
print(y_pred[0])

# check the actual label for the first test example
print(y_test[0])

NameError: name 'X_test_vec' is not defined

sample output array([ 0.06434628  0.34275846  0.50433091  0.07276319  0.01580115]

Because the posterior probability for category 2 (neutral) is the greatest, 0.50, the prediction should be "2". Because the actual label is also "2", this is a correct prediction


# Step 5.2 Error Analysis

In [39]:
# print out specific type of error for further analysis

# print out the very positive examples that are mistakenly predicted as negative
# according to the confusion matrix, there should be 53 such examples
# note if you use a different vectorizer option, your result might be different

err_cnt = 0
for i in range(0, len(y_test)):
    if(y_test[i]==4 and y_pred[i]==1):
        print(X_test[i])
        err_cnt = err_cnt+1
print("errors:", err_cnt)

NameError: name 'y_pred' is not defined

# Exercise D

In [40]:
# Can you find linguistic patterns in the above errors? 
# What kind of very positive examples were mistakenly predicted as negative?

# Can you write code to print out the errors that very negative examples were mistakenly predicted as very positive?
# Can you find lingustic patterns for this kind of errors?
# Based on the above error analysis, what suggestions would you give to improve the current model?

# Your code starts here
err_cnt = 0
for i in range(0, len(y_test)):
    if(y_test[i]==1 and y_pred[i]==4):
        print(X_test[i])
        err_cnt = err_cnt+1
print("errors:", err_cnt)
# Your code ends here

'''
this is the opposite of a truly magical movie .
achieves the remarkable feat of squandering a topnotch foursome of actors
a deeply unpleasant experience
hugely overwritten
is not Edward Burns ' best film
Once the expectation of laughter has been quashed by whatever obscenity is at hand , even the funniest idea is n't funny .
is a deeply unpleasant experience .
is hugely overwritten ,
is the opposite of a truly magical movie .
to this shocking testament to anti-Semitism and neo-fascism
is about as humorous as watching your favorite pet get buried alive
errors: 11
'''

NameError: name 'y_pred' is not defined

# Step 6: write the prediction output to file

In [34]:
y_pred=nb_clf.predict(X_test_vec)
output = open('prediction_output_2.csv', 'w')
for x, value in enumerate(y_pred):
    output.write(str(value) + '\n') 
output.close()

NameError: name 'X_test_vec' is not defined

# Step 6.1 Prepare submission to Kaggle sentiment classification competition

In [41]:
########## submit to Kaggle submission

# we are still using the model trained on 60% of the training data
# you can re-train the model on the entire data set 
#   and use the new model to predict the Kaggle test data
# below is sample code for using a trained model to predict Kaggle test data 
#    and format the prediction output for Kaggle submission

# read in the test data
# kaggle-sentiment/train.tsv
kaggle_test=p.read_csv("kaggle-sentiment/test.tsv", delimiter='\t') 

# preserve the id column of the test examples
kaggle_ids=kaggle_test['PhraseId'].values

# read in the text content of the examples
kaggle_X_test=kaggle_test['Phrase'].values

# vectorize the test examples using the vocabulary fitted from the 60% training data
kaggle_X_test_vec=unigram_count_vectorizer.transform(kaggle_X_test)

# predict using the NB classifier that we built
kaggle_pred=nb_clf.fit(X_train_vec, y_train).predict(kaggle_X_test_vec)

# combine the test example ids with their predictions
kaggle_submission=zip(kaggle_ids, kaggle_pred)

# prepare output file
outf=open('kaggle_submission_2.csv', 'w')

# write header
outf.write('PhraseId,Sentiment\n')

# write predictions with ids to the output file
for x, value in enumerate(kaggle_submission): outf.write(str(value[0]) + ',' + str(value[1]) + '\n')

# close the output file
outf.close()



NotFittedError: CountVectorizer - Vocabulary wasn't fitted.

In [42]:
test=p.read_csv("kaggle_submission_2.csv")
len(test)

66292

# Exercise E

In [43]:
# generate your Kaggle submissions with boolean representation and TF representation
# submit to Kaggle
# report your scores here
# which model gave better performance in the hold-out test
# which model gave better performance in the Kaggle test

Sample output:

(93636, 9968)
[[0 0 0 ..., 0 0 0]]
9968
[('disloc', 2484), ('surgeon', 8554), ('camaraderi', 1341), ('sketchiest', 7943), ('dedic', 2244), ('impud', 4376), ('adopt', 245), ('worker', 9850), ('buy', 1298), ('systemat', 8623)]
245

# BernoulliNB

In [44]:
from sklearn.naive_bayes import BernoulliNB
X_train_vec_bool = unigram_bool_vectorizer.fit_transform(X_train)
bernoulliNB_clf = BernoulliNB(X_train_vec_bool, y_train)

# Cross Validation

In [45]:
# cross validation

from sklearn.pipeline import Pipeline
from sklearn.model_selection import cross_val_score
nb_clf_pipe = Pipeline([('vect', CountVectorizer(encoding='latin-1', binary=False)),('nb', MultinomialNB())])
scores = cross_val_score(nb_clf_pipe, X, y, cv=3)
avg=sum(scores)/len(scores)
print(avg)

0.5595474569680894


# Exercise F

In [46]:
# run 3-fold cross validation to compare the performance of 
# (1) BernoulliNB (2) MultinomialNB with TF vectors (3) MultinomialNB with boolean vectors

# Your code starts here
nb_clf_pipe = Pipeline([('vect', CountVectorizer(encoding='latin-1', binary=False)),('nb', MultinomialNB())])
scores = cross_val_score(nb_clf_pipe, X, y, cv=3)
avg=sum(scores)/len(scores)
print(avg)
nb_clf_pipe = Pipeline([('vect', CountVectorizer(encoding='latin-1', binary=False)),('nb', BernoulliNB())])
scores = cross_val_score(nb_clf_pipe, X, y, cv=3)
avg=sum(scores)/len(scores)
print(avg)
nb_clf_pipe = Pipeline([('vect', CountVectorizer(encoding='latin-1', binary=True)),('nb', MultinomialNB())])
scores = cross_val_score(nb_clf_pipe, X, y, cv=3)
avg=sum(scores)/len(scores)
print(avg)


def runPipeline(classifier, boolean):
    nb_clf_pipe = Pipeline([('vect', CountVectorizer(encoding='latin-1', binary=boolean)),('nb', classifier)])
    scores = cross_val_score(nb_clf_pipe, X, y, cv=3)
    avg=sum(scores)/len(scores)
    print(classifier, boolean, avg)
    
runPipeline(BernoulliNB(), False)
runPipeline(MultinomialNB(), False)
runPipeline(MultinomialNB(), True)
    
    
    
    
# Your code ends here

'''
0.55315243657
0.553844611375
0.552306763002
0.560136963721
'''

0.5595474569680894
0.5531524365695574
0.5601369637205256
BernoulliNB(alpha=1.0, binarize=0.0, class_prior=None, fit_prior=True) False 0.5531524365695574
MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True) False 0.5595474569680894
MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True) True 0.5601369637205256


'\n0.55315243657\n0.553844611375\n0.552306763002\n0.560136963721\n'

In [47]:
my_string = "{}, is a {} science portal for {}"
  
print (my_string.format("GeeksforGeeks", "computer", "geeks")) 

GeeksforGeeks, is a computer science portal for geeks


In [48]:

def runPipeline(classifier, boolean):
    nb_clf_pipe = Pipeline([('vect', CountVectorizer(encoding='latin-1', binary=boolean)),('nb', classifier)])
    scores = cross_val_score(nb_clf_pipe, X, y, cv=3)
    avg=sum(scores)/len(scores)
    pretty_line = "{} | Accuracy using {} -- and booleans? {}"
    print(pretty_line.format(avg, classifier, boolean))
    
runPipeline(BernoulliNB(), False)
runPipeline(MultinomialNB(), False)
runPipeline(MultinomialNB(), True)

0.5531524365695574 | Accuracy using BernoulliNB(alpha=1.0, binarize=0.0, class_prior=None, fit_prior=True) -- and booleans? False
0.5595474569680894 | Accuracy using MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True) -- and booleans? False
0.5601369637205256 | Accuracy using MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True) -- and booleans? True


In [53]:
type(X)
X[0]

'A series of escapades demonstrating the adage that what is good for the goose is also good for the gander , some of which occasionally amuses but none of which amounts to much of a story .'

In [63]:
type(y)
y[:200]

array([1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3,
       3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
       2, 2, 3, 1, 2, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 4, 3, 2,
       4, 3, 2, 3, 3, 3, 2, 2, 4, 2, 3, 4, 2, 2, 2, 1, 2, 2, 2, 3, 2, 2,
       2, 2, 2, 2, 2, 2, 1, 2, 2, 2, 2, 2, 1, 0, 2, 0, 2, 1, 1, 1, 2, 2,
       1, 2, 2, 2, 2, 2, 3, 4, 4, 3, 3, 3, 3, 4, 2, 2, 2, 2, 2, 2, 2, 1,
       2, 3, 2, 1, 2, 1, 1, 2, 1, 1, 2, 2, 2, 1, 2, 2, 1, 2, 3, 3, 3, 1,
       2, 2, 1, 0, 2, 0, 1, 2, 1, 1, 2, 2, 4, 3, 2, 2, 3, 2, 4, 2, 3, 2,
       4, 3, 3, 3, 4, 2, 4, 4, 3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 2, 2,
       1, 2])

# Optional: use external linguistic resources such as stemmer

In [204]:
from sklearn.feature_extraction.text import CountVectorizer
import nltk.stem

english_stemmer = nltk.stem.SnowballStemmer('english')
class StemmedCountVectorizer(CountVectorizer):
    def build_analyzer(self):
        analyzer = super(StemmedCountVectorizer, self).build_analyzer()
        return lambda doc: ([english_stemmer.stem(w) for w in analyzer(doc)])

stem_vectorizer = StemmedCountVectorizer(min_df=3, analyzer="word")
X_train_stem_vec = stem_vectorizer.fit_transform(X_train)

In [194]:
# check the content of a document vector
print(X_train_stem_vec.shape)
print(X_train_stem_vec[0].toarray())

# check the size of the constructed vocabulary
print(len(stem_vectorizer.vocabulary_))

# print out the first 10 items in the vocabulary
print(list(stem_vectorizer.vocabulary_.items())[:10])

# check word index in vocabulary
print(stem_vectorizer.vocabulary_.get('adopt'))

(93636, 9968)
[[0 0 0 ..., 0 0 0]]
9968
[('disloc', 2484), ('surgeon', 8554), ('camaraderi', 1341), ('sketchiest', 7943), ('dedic', 2244), ('impud', 4376), ('adopt', 245), ('worker', 9850), ('buy', 1298), ('systemat', 8623)]
245
